In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [14]:
import datetime

stocks_table=pd.read_csv('cleaned_stocks.csv')
public_bonds_table=pd.read_csv('cleaned_public_bonds.csv')
corporate_bonds_table=pd.read_csv('cleaned_corporate_bonds.csv')
cash_table=pd.read_csv('cleaned_cash.csv')
gold_table=pd.read_csv('cleaned_gold.csv')

portfolios=pd.read_csv('portfolio_allocations.csv')
#print(portfolios)

# Removing the unnecessary column
del stocks_table['Unnamed: 0']
del public_bonds_table['Unnamed: 0']
del corporate_bonds_table['Unnamed: 0']
del cash_table['Unnamed: 0']
del gold_table['Unnamed: 0']

# # Removing the value for the 30th or 31st Dec 2019, that were needed for the interpolation
# stocks_table = stocks_table.drop([0])
# public_bonds_table = public_bonds_table.drop([0])
# corporate_bonds_table = corporate_bonds_table.drop([0])
# gold_table = gold_table.drop([0])

#0th element in the row is the index, Unnamed, so we don't need that
print(portfolios.loc[0][1], portfolios.loc[0][2], portfolios.loc[0][3], portfolios.loc[0][4], portfolios.loc[0][5])

# How to find the right column in a single input in the table
print(stocks_table.loc[0]["Date"])

# All the dates needed for the analysis
start_date = datetime.date(2020, 1, 1)
end_date = datetime.date(2020, 12, 31)
delta = datetime.timedelta(days=1)
dates = []

while start_date <= end_date:
  dates.append(start_date)
  start_date += delta

print(dates)

# Certain value of a date
print(dates[0].strftime("%d"))  

0 0 0 0 100
2020-01-01
[datetime.date(2020, 1, 1), datetime.date(2020, 1, 2), datetime.date(2020, 1, 3), datetime.date(2020, 1, 4), datetime.date(2020, 1, 5), datetime.date(2020, 1, 6), datetime.date(2020, 1, 7), datetime.date(2020, 1, 8), datetime.date(2020, 1, 9), datetime.date(2020, 1, 10), datetime.date(2020, 1, 11), datetime.date(2020, 1, 12), datetime.date(2020, 1, 13), datetime.date(2020, 1, 14), datetime.date(2020, 1, 15), datetime.date(2020, 1, 16), datetime.date(2020, 1, 17), datetime.date(2020, 1, 18), datetime.date(2020, 1, 19), datetime.date(2020, 1, 20), datetime.date(2020, 1, 21), datetime.date(2020, 1, 22), datetime.date(2020, 1, 23), datetime.date(2020, 1, 24), datetime.date(2020, 1, 25), datetime.date(2020, 1, 26), datetime.date(2020, 1, 27), datetime.date(2020, 1, 28), datetime.date(2020, 1, 29), datetime.date(2020, 1, 30), datetime.date(2020, 1, 31), datetime.date(2020, 2, 1), datetime.date(2020, 2, 2), datetime.date(2020, 2, 3), datetime.date(2020, 2, 4), datetime.

In [22]:
# Getting all the first days of the month and 31st of December
firstDaysOfMonth = []
for i in range(0, len(dates)):
  if(dates[i].strftime("%d") == "01" and (dates[i].strftime("%m") == "02" or dates[i].strftime("%m") == "04" or \
                                          dates[i].strftime("%m") == "07" or dates[i].strftime("%m") == "10")):
    firstDaysOfMonth.append(dates[i])
  elif(dates[i].strftime("%d") == "31" and dates[i].strftime("%m") == "12"):
    firstDaysOfMonth.append(dates[i])
print(firstDaysOfMonth)
print(len(firstDaysOfMonth))

[datetime.date(2020, 2, 1), datetime.date(2020, 4, 1), datetime.date(2020, 7, 1), datetime.date(2020, 10, 1), datetime.date(2020, 12, 31)]
5


## Investing the first day

In [23]:
import math

def calculating_return(original, current):
  return ((current - original) / original) * 100

assets = [stocks_table, corporate_bonds_table, public_bonds_table, gold_table, cash_table]

portfolio_results = {}

investing_money = 100000
for index in range(10626):

  # This is to get the percentage of each asset in an allocation
  # print(portfolios.loc[index])

  # Percentage of money for each asset
  stocks = (portfolios.loc[index][1] / 100) * investing_money
  corporate_bonds = (portfolios.loc[index][2] / 100) * investing_money
  public_bonds = (portfolios.loc[index][3] / 100) * investing_money
  gold = (portfolios.loc[index][4] / 100) * investing_money
  cash = (portfolios.loc[index][5] / 100) * investing_money

  # Buying shares the first day
  numOfStocks = math.floor(stocks / stocks_table.loc[0]["Price"])
  numOfCorpBonds = math.floor(corporate_bonds / corporate_bonds_table.loc[0]["Price"])
  numOfPubBonds = math.floor(public_bonds / public_bonds_table.loc[0]["Price"])
  numOfGold = math.floor(gold / gold_table.loc[0]["Price"])
  numOfCash = math.floor(cash / cash_table.loc[0]["Price"])

  asset_shares = [numOfStocks, numOfCorpBonds, numOfPubBonds, numOfGold, numOfCash]

  buy_amount = numOfStocks * stocks_table.loc[0]["Price"] \
              + numOfCorpBonds * corporate_bonds_table.loc[0]["Price"] \
              + numOfPubBonds * public_bonds_table.loc[0]["Price"] \
              + numOfGold * gold_table.loc[0]["Price"] \
              + numOfCash * cash_table.loc[0]["Price"]

  current_value = [0, 0, 0, 0, 0] # 1M, 3M, 6M, 9M, 12M

  for count, asset in enumerate(assets):
    for row in asset.itertuples(): #With this we get one row of the dataframe at a time, as a tuple (key: value pairs)
      # print(row[1]) # row[1] = gets us the date value
      # print(row[2]) # row[2] = gets us the price value
      # print(f"row[1] type: {type(row[1])}")
      for i in firstDaysOfMonth:
        # print(f"i type: {type(str(i))}")
        if(str(i) == row[1]):
          # print(f"Found the same day : {i}")
          if(i.strftime("%m") == "02"): # After one month
            current_value[0] += row[2] * asset_shares[count]
          elif(i.strftime("%m") == "04"): # After three months
            current_value[1] += row[2] * asset_shares[count]
          elif(i.strftime("%m") == "07"): # After six months
            current_value[2] += row[2] * asset_shares[count]
          elif(i.strftime("%m") == "10"): # After nine months
            current_value[3] += row[2] * asset_shares[count]
          elif(i.strftime("%m") == "12"): # After twelve months
            current_value[4] += row[2] * asset_shares[count]
        
  
  portfolio_results.update({index: [calculating_return(buy_amount, current_value[0]), \
                                   calculating_return(buy_amount, current_value[1]), \
                                   calculating_return(buy_amount, current_value[2]), \
                                   calculating_return(buy_amount, current_value[3]), \
                                   calculating_return(buy_amount, current_value[4])]})
  # print(f"Buy amount: {buy_amount}")
  # print(f"Current Value: {current_value}")


  # for i in firstDaysOfMonth:
  #   print(i)
  #   print(stocks_table["Date"])
  #   mask = (stocks_table['Date'] > i.st)
  #   filtered_df=df.loc[mask]
  #   print(filtered_df)

In [24]:
print(portfolio_results)

{0: [1.1792371269495543, 3.402842618528893, 0.8403361344537827, -2.7803714078224058, -6.691565515094935], 1: [1.311746606745872, 3.4418246333923146, 1.5893312602809546, -1.443038811628058, -5.174743489820731], 2: [1.4481329648402772, 3.481947159317076, 2.360240010349794, -0.0665793867153428, -3.613543247977179], 3: [1.584498571771388, 3.5220635806057263, 3.1310314667715855, 1.309670610108864, -2.0525805425088457], 4: [1.7208434322748174, 3.5621738986513884, 3.9017056563136516, 2.6857112266376033, -0.49185531920818437], 5: [1.8565137498532436, 3.6020857777448296, 4.668567066847297, 4.054944117088822, 1.061148482446308], 6: [1.9926857393560784, 3.6421452401088876, 5.438264122247457, 5.429240058260222, 2.6198948696545457], 7: [2.128837036586506, 3.6821986151615236, 6.207844216874802, 6.803327165690834, 4.178404394605336], 8: [2.262630459797698, 3.721558344142882, 6.964096690335342, 8.153617773516162, 5.709923584595026], 9: [2.398936104057066, 3.761657125442565, 7.73454921441096, 9.5292626

In [25]:
best_returns_for_each_period = {0: [portfolio_results[0][0], 0], 1: [portfolio_results[0][1], 0], \
                                2: [portfolio_results[0][2], 0], 3: [portfolio_results[0][3], 0], \
                                4: [portfolio_results[0][4], 0]}
for key in portfolio_results:

  # Checking for the 1M
  if portfolio_results[key][0] > best_returns_for_each_period[0][0]:
    best_returns_for_each_period[0][0] = portfolio_results[key][0]
    best_returns_for_each_period[0][1] = key

  # Checking for the 3M
  if portfolio_results[key][1] > best_returns_for_each_period[1][0]:
    best_returns_for_each_period[1][0] = portfolio_results[key][1]
    best_returns_for_each_period[1][1] = key

  # Checking for the 6M
  if portfolio_results[key][2] > best_returns_for_each_period[2][0]:
    best_returns_for_each_period[2][0] = portfolio_results[key][2]
    best_returns_for_each_period[2][1] = key
  
  # Checking for the 9M
  if portfolio_results[key][3] > best_returns_for_each_period[3][0]:
    best_returns_for_each_period[3][0] = portfolio_results[key][3]
    best_returns_for_each_period[3][1] = key
  
  # Checking for the 12M
  if portfolio_results[key][4] > best_returns_for_each_period[4][0]:
    best_returns_for_each_period[4][0] = portfolio_results[key][4]
    best_returns_for_each_period[4][1] = key

print(best_returns_for_each_period)

def print_function(month, value, port_index):
  print(f"Best return for {month} month(s) period {value},that is for the portfolio allocation: {portfolios.loc[port_index][1]}-{portfolios.loc[port_index][2]}-{portfolios.loc[port_index][3]}-{portfolios.loc[port_index][4]}-{portfolios.loc[port_index][5]}")

print_function(1, best_returns_for_each_period[0][0], best_returns_for_each_period[0][1])
print_function(3, best_returns_for_each_period[1][0], best_returns_for_each_period[1][1])
print_function(6, best_returns_for_each_period[2][0], best_returns_for_each_period[2][1])
print_function(9, best_returns_for_each_period[3][0], best_returns_for_each_period[3][1])
print_function(12, best_returns_for_each_period[4][0], best_returns_for_each_period[4][1])

{0: [3.8916971704142793, 20], 1: [5.713269017871279, 230], 2: [16.172215443611638, 20], 3: [24.594735924699307, 20], 4: [24.35767822903957, 20]}
Best return for 1 month(s) period 3.8916971704142793,that is for the portfolio allocation: 0-0-0-100-0
Best return for 3 month(s) period 5.713269017871279,that is for the portfolio allocation: 0-0-100-0-0
Best return for 6 month(s) period 16.172215443611638,that is for the portfolio allocation: 0-0-0-100-0
Best return for 9 month(s) period 24.594735924699307,that is for the portfolio allocation: 0-0-0-100-0
Best return for 12 month(s) period 24.35767822903957,that is for the portfolio allocation: 0-0-0-100-0


## Investing the first day with *rebalance*

In [29]:
import math

portfolio_results_rebalance = {}

for index in range(10626):

  # print(portfolios.loc[index])

  # Percentage of money for each asset
  stocks = (portfolios.loc[index][1] / 100) * investing_money
  corporate_bonds = (portfolios.loc[index][2] / 100) * investing_money
  public_bonds = (portfolios.loc[index][3] / 100) * investing_money
  gold = (portfolios.loc[index][4] / 100) * investing_money
  cash = (portfolios.loc[index][5] / 100) * investing_money

  # Buying shares the first day
  numOfStocks = stocks / stocks_table.loc[0]["Price"]
  numOfCorpBonds = corporate_bonds / corporate_bonds_table.loc[0]["Price"]
  numOfPubBonds = public_bonds / public_bonds_table.loc[0]["Price"]
  numOfGold = gold / gold_table.loc[0]["Price"]
  numOfCash = cash / cash_table.loc[0]["Price"]

  current_value = [0, 0, 0, 0, 0] # 1M, 3M, 6M, 9M, 12M

  # stringCheck = "2020-03-01"
  # print(stringCheck[5:7]) # To check the month
  # print(stringCheck[8:10])# To check the day

  for row in stocks_table.itertuples():
    # print(row[1]) # row[1] = gets us the date value
    # print(row[2]) # row[2] = gets us the price value
    # print(row[0]) # row[0] = gets the current index

    # Checking if its the first day of the month
    if(row[1][8:10] == "01" and row[1][5:7] != "01"):
      if(row[1][5:7] == "02"):
        current_value[0] += row[2] * numOfStocks # For stocks
        current_value[0] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds # For corporate bonds
        current_value[0] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds # For public bonds
        current_value[0] += gold_table.loc[row[0]]["Price"] * numOfGold # For gold
        current_value[0] += cash_table.loc[row[0]-1]["Price"] * numOfCash # For cash
      if(row[1][5:7] == "04"):
        current_value[1] += row[2] * numOfStocks
        current_value[1] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds
        current_value[1] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds
        current_value[1] += gold_table.loc[row[0]]["Price"] * numOfGold
        current_value[1] += cash_table.loc[row[0]-1]["Price"] * numOfCash
      if(row[1][5:7] == "07"):
        current_value[2] += row[2] * numOfStocks
        current_value[2] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds
        current_value[2] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds
        current_value[2] += gold_table.loc[row[0]]["Price"] * numOfGold
        current_value[2] += cash_table.loc[row[0]-1]["Price"] * numOfCash
      if(row[1][5:7] == "10"):
        current_value[3] += row[2] * numOfStocks
        current_value[3] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds
        current_value[3] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds
        current_value[3] += gold_table.loc[row[0]]["Price"] * numOfGold
        current_value[3] += cash_table.loc[row[0]-1]["Price"] * numOfCash
    elif(row[1][8:10] == "31" and row[1][5:7] == "12"):
        current_value[4] += row[2] * numOfStocks
        current_value[4] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds
        current_value[4] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds
        current_value[4] += gold_table.loc[row[0]]["Price"] * numOfGold
        current_value[4] += cash_table.loc[row[0]-1]["Price"] * numOfCash
    
    # Checking if its the 15th of the month (info needed for rebalance)
    if(row[1][8:10] == "15"):
      currentStockValue = numOfStocks * stocks_table.loc[row[0]]["Price"]
      currentCorpBonds = numOfCorpBonds * corporate_bonds_table.loc[row[0]]["Price"]
      currentPubBonds = numOfPubBonds * public_bonds_table.loc[row[0]]["Price"]
      currentGold = numOfGold * gold_table.loc[row[0]]["Price"]
      currentCash = numOfCash * cash_table.loc[row[0]]["Price"]

      currentAmount = currentStockValue + currentCorpBonds + currentPubBonds + \
                      currentGold + currentCash

      difference = 0
      numOfShares = 0

      if(currentStockValue / currentAmount > portfolios.loc[index][1] / 100):
        difference = currentStockValue - (portfolios.loc[index][1] / 100) * currentAmount
        numOfShares = difference / stocks_table.loc[row[0]]["Price"]
        numOfStocks -= numOfShares
      else:
        difference = (portfolios.loc[index][1] / 100) * currentAmount - currentStockValue
        numOfShares = difference / stocks_table.loc[row[0]]["Price"]
        numOfStocks += numOfShares

      if(currentCorpBonds / currentAmount > portfolios.loc[index][2] / 100):
        difference = currentCorpBonds - (portfolios.loc[index][2] / 100) * currentAmount
        numOfShares = difference / corporate_bonds_table.loc[row[0]]["Price"]
        numOfCorpBonds -= numOfShares
      else:
        difference = (portfolios.loc[index][2] / 100) * currentAmount - currentCorpBonds
        numOfShares = difference / corporate_bonds_table.loc[row[0]]["Price"]
        numOfCorpBonds += numOfShares
      
      if(currentPubBonds / currentAmount > portfolios.loc[index][3] / 100):
        difference = currentPubBonds - (portfolios.loc[index][3] / 100) * currentAmount
        numOfShares = difference / public_bonds_table.loc[row[0]]["Price"]
        numOfPubBonds -= numOfShares
      else:
        difference = (portfolios.loc[index][3] / 100) * currentAmount - currentPubBonds
        numOfShares = difference / public_bonds_table.loc[row[0]]["Price"]
        numOfPubBonds += numOfShares
      
      if(currentGold / currentAmount > portfolios.loc[index][4] / 100):
        difference = currentGold - (portfolios.loc[index][4] / 100) * currentAmount
        numOfShares = difference / gold_table.loc[row[0]]["Price"]
        numOfGold -= numOfShares
      else:
        difference = (portfolios.loc[index][4] / 100) * currentAmount - currentGold
        numOfShares = difference / gold_table.loc[row[0]]["Price"]
        numOfGold += numOfShares
      
      if(currentCash / currentAmount > portfolios.loc[index][5] / 100):
        difference = currentCash - (portfolios.loc[index][5] / 100) * currentAmount
        numOfShares = difference / cash_table.loc[row[0]]["Price"]
        numOfCash -= numOfShares
      else:
        difference = (portfolios.loc[index][5] / 100) * currentAmount - currentCash
        numOfShares = difference / cash_table.loc[row[0]]["Price"]
        numOfCash += numOfShares
  portfolio_results_rebalance.update({index: [calculating_return(100000, current_value[0]), \
                                   calculating_return(100000, current_value[1]), \
                                   calculating_return(100000, current_value[2]), \
                                   calculating_return(100000, current_value[3]), \
                                   calculating_return(100000, current_value[4])]})
  # print(f"Buy amount: {buy_amount}")
  # print(f"Current Value: {current_value}")

In [30]:
print(portfolio_results_rebalance)

{0: [1.0374520178441744, 2.7596223674654903, 1.0374520178441744, -2.5936300446104434, -6.961303039734412], 1: [1.1792261760898692, 2.840280571815223, 1.7872001507523383, -1.3086210355078802, -5.523977508176249], 2: [1.3210990816389967, 2.9200449970029005, 2.53777899396015, -0.01553384143760195, -4.073230074132822], 3: [1.4630707344915863, 2.998913743999976, 3.28917313450409, 1.2855940951776283, -2.6090368299014224], 4: [1.6051411346476525, 3.0768849134253977, 4.04136706450209, 2.5947245103644967, -1.1313748583655396], 5: [1.7473102821071809, 3.153956605545347, 4.79434518092571, 3.911818318191741, 0.35977775753432073], 6: [1.8895781768701128, 3.230126920273513, 5.5480917853736464, 5.23683561040883, 1.864441925346444], 7: [2.031944818936521, 3.3053939571709927, 6.3025910838435815, 6.569735656126927, 3.3826375336653722], 8: [2.174410208306421, 3.379755815446275, 7.0578271865046265, 7.910476901545102, 4.914383442706429], 9: [2.316974344979739, 3.4532105939551547, 7.813784107469256, 9.25901

In [31]:
best_returns_for_each_period = {0: [portfolio_results_rebalance[0][0], 0], 1: [portfolio_results_rebalance[0][1], 0], \
                                2: [portfolio_results_rebalance[0][2], 0], 3: [portfolio_results_rebalance[0][3], 0], \
                                4: [portfolio_results_rebalance[0][4], 0]}
for key in portfolio_results_rebalance:
  
  # Checking for the 1M
  if portfolio_results_rebalance[key][0] > best_returns_for_each_period[0][0]:
    best_returns_for_each_period[0][0] = portfolio_results_rebalance[key][0]
    best_returns_for_each_period[0][1] = key

  # Checking for the 3M
  if portfolio_results_rebalance[key][1] > best_returns_for_each_period[1][0]:
    best_returns_for_each_period[1][0] = portfolio_results_rebalance[key][1]
    best_returns_for_each_period[1][1] = key

  # Checking for the 6M
  if portfolio_results_rebalance[key][2] > best_returns_for_each_period[2][0]:
    best_returns_for_each_period[2][0] = portfolio_results_rebalance[key][2]
    best_returns_for_each_period[2][1] = key
  
  # Checking for the 9M
  if portfolio_results_rebalance[key][3] > best_returns_for_each_period[3][0]:
    best_returns_for_each_period[3][0] = portfolio_results_rebalance[key][3]
    best_returns_for_each_period[3][1] = key
  
  # Checking for the 12M
  if portfolio_results_rebalance[key][4] > best_returns_for_each_period[4][0]:
    best_returns_for_each_period[4][0] = portfolio_results_rebalance[key][4]
    best_returns_for_each_period[4][1] = key

print(best_returns_for_each_period)
print_function(1, best_returns_for_each_period[0][0], best_returns_for_each_period[0][1])
print_function(3, best_returns_for_each_period[1][0], best_returns_for_each_period[1][1])
print_function(6, best_returns_for_each_period[2][0], best_returns_for_each_period[2][1])
print_function(9, best_returns_for_each_period[3][0], best_returns_for_each_period[3][1])
print_function(12, best_returns_for_each_period[4][0], best_returns_for_each_period[4][1])

{0: [3.891697170414278, 20], 1: [5.713269017871266, 230], 2: [16.17221544361164, 20], 3: [24.594735924699314, 20], 4: [24.35767822903958, 20]}
Best return for 1 month(s) period 3.891697170414278,that is for the portfolio allocation: 0-0-0-100-0
Best return for 3 month(s) period 5.713269017871266,that is for the portfolio allocation: 0-0-100-0-0
Best return for 6 month(s) period 16.17221544361164,that is for the portfolio allocation: 0-0-0-100-0
Best return for 9 month(s) period 24.594735924699314,that is for the portfolio allocation: 0-0-0-100-0
Best return for 12 month(s) period 24.35767822903958,that is for the portfolio allocation: 0-0-0-100-0


## Investing using DCA (Dollar Cost Averaging)

In [37]:
import math

portfolio_results_DCA = {}

for index in range(10626):

  # Percentage of money for each asset
  stocks = (portfolios.loc[index][1] / 100) * investing_money
  corporate_bonds = (portfolios.loc[index][2] / 100) * investing_money
  public_bonds = (portfolios.loc[index][3] / 100) * investing_money
  gold = (portfolios.loc[index][4] / 100) * investing_money
  cash = (portfolios.loc[index][5] / 100) * investing_money

  current_value = [0, 0, 0, 0, 0] # 1M, 3M, 6M, 9M, 12M

  # stringCheck = "2020-03-01"
  # print(stringCheck[5:7]) # To check the month
  # print(stringCheck[8:10])# To check the day

  DCA_num_of_months = [1, 3, 6, 9, 12]

  for DCAmonths in DCA_num_of_months:

    # Buying shares the first day
    numOfStocks = (stocks / DCAmonths) / stocks_table.loc[0]["Price"]
    numOfCorpBonds = (corporate_bonds / DCAmonths) / corporate_bonds_table.loc[0]["Price"]
    numOfPubBonds = (public_bonds / DCAmonths) / public_bonds_table.loc[0]["Price"]
    numOfGold = (gold / DCAmonths) / gold_table.loc[0]["Price"]
    numOfCash = (cash / DCAmonths) / cash_table.loc[0]["Price"]

    finished = False

    for row in stocks_table.itertuples():
      # print(row[1]) # row[1] = gets us the date value
      # print(row[2]) # row[2] = gets us the price value
      # print(row[0]) # row[0] = gets the current index

      if (finished == True):
        continue

      # Checking if its the first day of the month
      if(row[1][8:10] == "01" and row[1][5:7] != "01"):
        if(row[1][5:7] == "02" and DCAmonths == 1):
          current_value[0] += row[2] * numOfStocks # For stocks
          current_value[0] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds # For corporate bonds
          current_value[0] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds # For public bonds
          current_value[0] += gold_table.loc[row[0]]["Price"] * numOfGold # For gold
          current_value[0] += cash_table.loc[row[0]-1]["Price"] * numOfCash # For cash
          finished = True
        elif(row[1][5:7] == "04" and DCAmonths == 3):
          current_value[1] += row[2] * numOfStocks
          current_value[1] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds
          current_value[1] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds
          current_value[1] += gold_table.loc[row[0]]["Price"] * numOfGold
          current_value[1] += cash_table.loc[row[0]-1]["Price"] * numOfCash
          finished = True
        elif(row[1][5:7] == "07" and DCAmonths == 6):
          current_value[2] += row[2] * numOfStocks
          current_value[2] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds
          current_value[2] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds
          current_value[2] += gold_table.loc[row[0]]["Price"] * numOfGold
          current_value[2] += cash_table.loc[row[0]-1]["Price"] * numOfCash
          finished = True
        elif(row[1][5:7] == "10" and DCAmonths == 9):
          current_value[3] += row[2] * numOfStocks
          current_value[3] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds
          current_value[3] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds
          current_value[3] += gold_table.loc[row[0]]["Price"] * numOfGold
          current_value[3] += cash_table.loc[row[0]-1]["Price"] * numOfCash
          finished = True
        
        if (finished == True):
          continue
        
        numOfStocks += (stocks / DCAmonths) / stocks_table.loc[row[0]]["Price"]
        numOfCorpBonds += (corporate_bonds / DCAmonths) / corporate_bonds_table.loc[row[0]]["Price"]
        numOfPubBonds += (public_bonds / DCAmonths) / public_bonds_table.loc[row[0]]["Price"]
        numOfGold += (gold / DCAmonths) / gold_table.loc[row[0]]["Price"]
        numOfCash += (cash / DCAmonths) / cash_table.loc[row[0]-1]["Price"]

      elif(row[1][8:10] == "31" and row[1][5:7] == "12"):
        current_value[4] += row[2] * numOfStocks
        current_value[4] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds
        current_value[4] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds
        current_value[4] += gold_table.loc[row[0]]["Price"] * numOfGold
        current_value[4] += cash_table.loc[row[0]-1]["Price"] * numOfCash
     
  portfolio_results_DCA.update({index: [calculating_return(100000, current_value[0]), \
                                   calculating_return(100000, current_value[1]), \
                                   calculating_return(100000, current_value[2]), \
                                   calculating_return(100000, current_value[3]), \
                                   calculating_return(100000, current_value[4])]})

In [38]:
print(portfolio_results_DCA)

{0: [1.0374520178441744, 1.8887812204550576, -0.5668143129918463, -2.884166665998753, -6.390318341648715], 1: [1.180164275472678, 1.8751710098627516, -0.05971035266268882, -2.1549241662539136, -5.618364912755511], 2: [1.3228765331011818, 1.8615607992704464, 0.44739360766646863, -1.4256816665090593, -4.846411483862277], 3: [1.4655887907296856, 1.8479505886781555, 0.954497567995626, -0.6964391667641903, -4.074458054969102], 4: [1.6083010483581892, 1.834340378085879, 1.461601528324798, 0.032803332980634876, -3.3025046260758537], 5: [1.7510133059866932, 1.8207301674935588, 1.9687054886539552, 0.7620458327255037, -2.5305511971826347], 6: [1.8937255636151968, 1.8071199569012535, 2.4758094489830835, 1.4912883324703434, -1.7585977682894154], 7: [2.0364378212437004, 1.7935097463089622, 2.9829134093122702, 2.220530832215183, -0.9866443393962109], 8: [2.1791500788722185, 1.779899535716657, 3.490017369641427, 2.9497733319600377, -0.2146909105029772], 9: [2.3218623365007223, 1.766289325124366, 3.99

In [40]:
best_returns_for_each_period = {0: [portfolio_results_DCA[0][0], 0], 1: [portfolio_results_DCA[0][1], 0], \
                                2: [portfolio_results_DCA[0][2], 0], 3: [portfolio_results_DCA[0][3], 0], \
                                4: [portfolio_results_DCA[0][4], 0]}
for key in portfolio_results_DCA:
  
  # Checking for the 1M
  if portfolio_results_DCA[key][0] > best_returns_for_each_period[0][0]:
    best_returns_for_each_period[0][0] = portfolio_results_DCA[key][0]
    best_returns_for_each_period[0][1] = key

  # Checking for the 3M
  if portfolio_results_DCA[key][1] > best_returns_for_each_period[1][0]:
    best_returns_for_each_period[1][0] = portfolio_results_DCA[key][1]
    best_returns_for_each_period[1][1] = key

  # Checking for the 6M
  if portfolio_results_DCA[key][2] > best_returns_for_each_period[2][0]:
    best_returns_for_each_period[2][0] = portfolio_results_DCA[key][2]
    best_returns_for_each_period[2][1] = key
  
  # Checking for the 9M
  if portfolio_results_DCA[key][3] > best_returns_for_each_period[3][0]:
    best_returns_for_each_period[3][0] = portfolio_results_DCA[key][3]
    best_returns_for_each_period[3][1] = key
  
  # Checking for the 12M
  if portfolio_results_DCA[key][4] > best_returns_for_each_period[4][0]:
    best_returns_for_each_period[4][0] = portfolio_results_DCA[key][4]
    best_returns_for_each_period[4][1] = key

print(best_returns_for_each_period)

print_function(1, best_returns_for_each_period[0][0], best_returns_for_each_period[0][1])
print_function(3, best_returns_for_each_period[1][0], best_returns_for_each_period[1][1])
print_function(6, best_returns_for_each_period[2][0], best_returns_for_each_period[2][1])
print_function(9, best_returns_for_each_period[3][0], best_returns_for_each_period[3][1])
print_function(12, best_returns_for_each_period[4][0], best_returns_for_each_period[4][1])

{0: [3.891697170414278, 20], 1: [3.338607109858189, 230], 2: [9.575264893591331, 20], 3: [11.700683328898217, 20], 4: [12.184322591098592, 10625]}
Best return for 1 month(s) period 3.891697170414278,that is for the portfolio allocation: 0-0-0-100-0
Best return for 3 month(s) period 3.338607109858189,that is for the portfolio allocation: 0-0-100-0-0
Best return for 6 month(s) period 9.575264893591331,that is for the portfolio allocation: 0-0-0-100-0
Best return for 9 month(s) period 11.700683328898217,that is for the portfolio allocation: 0-0-0-100-0
Best return for 12 month(s) period 12.184322591098592,that is for the portfolio allocation: 100-0-0-0-0


# Investing using DCA with *rebalance*

In [46]:
import math

portfolio_results_DCA_rebalance = {}

for index in range(10626):

  # Percentage of money for each asset
  stocks = (portfolios.loc[index][1] / 100) * investing_money
  corporate_bonds = (portfolios.loc[index][2] / 100) * investing_money
  public_bonds = (portfolios.loc[index][3] / 100) * investing_money
  gold = (portfolios.loc[index][4] / 100) * investing_money
  cash = (portfolios.loc[index][5] / 100) * investing_money

  current_value = [0, 0, 0, 0, 0] # 1M, 3M, 6M, 9M, 12M

  DCA_num_of_months = [1, 3, 6, 9, 12]

  for DCAmonths in DCA_num_of_months:

    # Buying shares the first day
    numOfStocks = (stocks / DCAmonths) / stocks_table.loc[0]["Price"]
    numOfCorpBonds = (corporate_bonds / DCAmonths) / corporate_bonds_table.loc[0]["Price"]
    numOfPubBonds = (public_bonds / DCAmonths) / public_bonds_table.loc[0]["Price"]
    numOfGold = (gold / DCAmonths) / gold_table.loc[0]["Price"]
    numOfCash = (cash / DCAmonths) / cash_table.loc[0]["Price"]

    finished = False

    for row in stocks_table.itertuples():
      # print(row[1]) # row[1] = gets us the date value
      # print(row[2]) # row[2] = gets us the price value
      # print(row[0]) # row[0] = gets the current index

      if (finished == True):
        continue

      # Checking if its the first day of the month
      if(row[1][8:10] == "01" and row[1][5:7] != "01"):
        if(row[1][5:7] == "02" and DCAmonths == 1):
          current_value[0] += row[2] * numOfStocks # For stocks
          current_value[0] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds # For corporate bonds
          current_value[0] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds # For public bonds
          current_value[0] += gold_table.loc[row[0]]["Price"] * numOfGold # For gold
          current_value[0] += cash_table.loc[row[0]-1]["Price"] * numOfCash # For cash
          finished = True
        if(row[1][5:7] == "04" and DCAmonths == 3):
          current_value[1] += row[2] * numOfStocks
          current_value[1] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds
          current_value[1] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds
          current_value[1] += gold_table.loc[row[0]]["Price"] * numOfGold
          current_value[1] += cash_table.loc[row[0]-1]["Price"] * numOfCash
          finished = True
        if(row[1][5:7] == "07" and DCAmonths == 6):
          current_value[2] += row[2] * numOfStocks
          current_value[2] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds
          current_value[2] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds
          current_value[2] += gold_table.loc[row[0]]["Price"] * numOfGold
          current_value[2] += cash_table.loc[row[0]-1]["Price"] * numOfCash
          finished = True
        if(row[1][5:7] == "10" and DCAmonths == 9):
          current_value[3] += row[2] * numOfStocks
          current_value[3] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds
          current_value[3] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds
          current_value[3] += gold_table.loc[row[0]]["Price"] * numOfGold
          current_value[3] += cash_table.loc[row[0]-1]["Price"] * numOfCash
          finished = True

        if (finished == True):
          continue
        
        numOfStocks += (stocks / DCAmonths) / stocks_table.loc[row[0]]["Price"]
        numOfCorpBonds += (corporate_bonds / DCAmonths) / corporate_bonds_table.loc[row[0]]["Price"]
        numOfPubBonds += (public_bonds / DCAmonths) / public_bonds_table.loc[row[0]]["Price"]
        numOfGold += (gold / DCAmonths) / gold_table.loc[row[0]]["Price"]
        numOfCash += (cash / DCAmonths) / cash_table.loc[row[0]-1]["Price"]

      elif(row[1][8:10] == "31" and row[1][5:7] == "12"):
        current_value[4] += row[2] * numOfStocks
        current_value[4] += corporate_bonds_table.loc[row[0]]["Price"] * numOfCorpBonds
        current_value[4] += public_bonds_table.loc[row[0]]["Price"] * numOfPubBonds
        current_value[4] += gold_table.loc[row[0]]["Price"] * numOfGold
        current_value[4] += cash_table.loc[row[0]-1]["Price"] * numOfCash
        
      # Checking if its the 15th of the month (info needed for rebalance)
      if(row[1][8:10] == "15"):
        currentStockValue = numOfStocks * stocks_table.loc[row[0]]["Price"]
        currentCorpBonds = numOfCorpBonds * corporate_bonds_table.loc[row[0]]["Price"]
        currentPubBonds = numOfPubBonds * public_bonds_table.loc[row[0]]["Price"]
        currentGold = numOfGold * gold_table.loc[row[0]]["Price"]
        currentCash = numOfCash * cash_table.loc[row[0]-1]["Price"]

        currentAmount = currentStockValue + currentCorpBonds + currentPubBonds + \
                        currentGold + currentCash

        difference = 0
        numOfShares = 0

        if(currentStockValue / currentAmount > portfolios.loc[index][1] / 100):
          difference = currentStockValue - (portfolios.loc[index][1] / 100) * currentAmount
          numOfShares = difference / stocks_table.loc[row[0]]["Price"]
          numOfStocks -= numOfShares
        else:
          difference = (portfolios.loc[index][1] / 100) * currentAmount - currentStockValue
          numOfShares = difference / stocks_table.loc[row[0]]["Price"]
          numOfStocks += numOfShares

        if(currentCorpBonds / currentAmount > portfolios.loc[index][2] / 100):
          difference = currentCorpBonds - (portfolios.loc[index][2] / 100) * currentAmount
          numOfShares = difference / corporate_bonds_table.loc[row[0]]["Price"]
          numOfCorpBonds -= numOfShares
        else:
          difference = (portfolios.loc[index][2] / 100) * currentAmount - currentCorpBonds
          numOfShares = difference / corporate_bonds_table.loc[row[0]]["Price"]
          numOfCorpBonds += numOfShares
        
        if(currentPubBonds / currentAmount > portfolios.loc[index][3] / 100):
          difference = currentPubBonds - (portfolios.loc[index][3] / 100) * currentAmount
          numOfShares = difference / public_bonds_table.loc[row[0]]["Price"]
          numOfPubBonds -= numOfShares
        else:
          difference = (portfolios.loc[index][3] / 100) * currentAmount - currentPubBonds
          numOfShares = difference / public_bonds_table.loc[row[0]]["Price"]
          numOfPubBonds += numOfShares
        
        if(currentGold / currentAmount > portfolios.loc[index][4] / 100):
          difference = currentGold - (portfolios.loc[index][4] / 100) * currentAmount
          numOfShares = difference / gold_table.loc[row[0]]["Price"]
          numOfGold -= numOfShares
        else:
          difference = (portfolios.loc[index][4] / 100) * currentAmount - currentGold
          numOfShares = difference / gold_table.loc[row[0]]["Price"]
          numOfGold += numOfShares
        
        if(currentCash / currentAmount > portfolios.loc[index][5] / 100):
          difference = currentCash - (portfolios.loc[index][5] / 100) * currentAmount
          numOfShares = difference / cash_table.loc[row[0]]["Price"]
          numOfCash -= numOfShares
        else:
          difference = (portfolios.loc[index][5] / 100) * currentAmount - currentCash
          numOfShares = difference / cash_table.loc[row[0]]["Price"]
          numOfCash += numOfShares
     
  portfolio_results_DCA_rebalance.update({index: [calculating_return(100000, current_value[0]), \
                                   calculating_return(100000, current_value[1]), \
                                   calculating_return(100000, current_value[2]), \
                                   calculating_return(100000, current_value[3]), \
                                   calculating_return(100000, current_value[4])]})

In [47]:
print(portfolio_results_DCA_rebalance)

{0: [1.0374520178441744, 1.8887812204550576, -0.5668143129918463, -2.884166665998753, -6.390318341648715], 1: [1.1793309529940015, 1.8847343974099202, -0.06130921774334274, -2.18274972989285, -5.66266617918617], 2: [1.3212976062995003, 1.8796806652103841, 0.4444142485163756, -1.4782531525224332, -4.93034524098289], 3: [1.463351977760627, 1.8736200635992426, 0.9503478527355329, -0.770700885337661, -4.193355066864125], 4: [1.6054940673774256, 1.8665526322536752, 1.4564833355899318, -0.060117153964689356, -3.4516955144949892], 5: [1.7477238751498516, 1.8584784107849992, 1.9628124114683159, 0.6534735425680119, -2.7053667611343846], 6: [1.8900414010779205, 1.8493974387388736, 2.469326768458617, 1.3700464326162183, -1.9543693053758762], 7: [2.0324466451616607, 1.8393097555953426, 2.976018068333244, 2.089576472717992, -1.1987039688780787], 8: [2.1749396074010585, 1.828215400768502, 3.4828779465351545, 2.8120383484036573, -0.43837189808295807], 9: [2.3175202877960985, 1.8161144136069052, 3.989

In [48]:
best_returns_for_each_period = {0: [portfolio_results_DCA_rebalance[0][0], 0], 1: [portfolio_results_DCA_rebalance[0][1], 0], \
                                2: [portfolio_results_DCA_rebalance[0][2], 0], 3: [portfolio_results_DCA_rebalance[0][3], 0], \
                                4: [portfolio_results_DCA_rebalance[0][4], 0]}
for key in portfolio_results_DCA_rebalance:
  
  # Checking for the 1M
  if portfolio_results_DCA_rebalance[key][0] > best_returns_for_each_period[0][0]:
    best_returns_for_each_period[0][0] = portfolio_results_DCA_rebalance[key][0]
    best_returns_for_each_period[0][1] = key

  # Checking for the 3M
  if portfolio_results_DCA_rebalance[key][1] > best_returns_for_each_period[1][0]:
    best_returns_for_each_period[1][0] = portfolio_results_DCA_rebalance[key][1]
    best_returns_for_each_period[1][1] = key

  # Checking for the 6M
  if portfolio_results_DCA_rebalance[key][2] > best_returns_for_each_period[2][0]:
    best_returns_for_each_period[2][0] = portfolio_results_DCA_rebalance[key][2]
    best_returns_for_each_period[2][1] = key
  
  # Checking for the 9M
  if portfolio_results_DCA_rebalance[key][3] > best_returns_for_each_period[3][0]:
    best_returns_for_each_period[3][0] = portfolio_results_DCA_rebalance[key][3]
    best_returns_for_each_period[3][1] = key

  # Checking for the 12M
  if portfolio_results_DCA_rebalance[key][4] > best_returns_for_each_period[4][0]:
    best_returns_for_each_period[4][0] = portfolio_results_DCA_rebalance[key][4]
    best_returns_for_each_period[4][1] = key

print(best_returns_for_each_period)

print_function(1, best_returns_for_each_period[0][0], best_returns_for_each_period[0][1])
print_function(3, best_returns_for_each_period[1][0], best_returns_for_each_period[1][1])
print_function(6, best_returns_for_each_period[2][0], best_returns_for_each_period[2][1])
print_function(9, best_returns_for_each_period[3][0], best_returns_for_each_period[3][1])
print_function(12, best_returns_for_each_period[4][0], best_returns_for_each_period[4][1])

{0: [3.891697170414278, 20], 1: [3.338607109858189, 230], 2: [9.575264893591331, 20], 3: [11.700683328898217, 20], 4: [12.184322591098592, 10625]}
Best return for 1 month(s) period 3.891697170414278,that is for the portfolio allocation: 0-0-0-100-0
Best return for 3 month(s) period 3.338607109858189,that is for the portfolio allocation: 0-0-100-0-0
Best return for 6 month(s) period 9.575264893591331,that is for the portfolio allocation: 0-0-0-100-0
Best return for 9 month(s) period 11.700683328898217,that is for the portfolio allocation: 0-0-0-100-0
Best return for 12 month(s) period 12.184322591098592,that is for the portfolio allocation: 100-0-0-0-0


In [50]:
final_array_return=[]
df2=pd.DataFrame(columns=['1-OFF-1M', '1-OFF-3M','1-OFF-6M', '1-OFF-9M', '1-OFF-12M',
                           '1-OFF-REB-1M', '1-OFF-REB-3M', '1-OFF-REB-6M', '1-OFF-REB-9M', '1-OFF-REB-12M',
                           'DCA-1M', 'DCA-3M', 'DCA-6M', 'DCA-9M', 'DCA-12M',
                           'DCA-REB-1M', 'DCA-REB-3M', 'DCA-REB-6M', 'DCA-REB-9M', 'DCA-REB-12M'])
for i in range(10626):
  final_array_return+=[[portfolio_results[i][0],portfolio_results[i][1],portfolio_results[i][2],portfolio_results[i][3],portfolio_results[i][4],
                            portfolio_results_rebalance[i][0],portfolio_results_rebalance[i][1],portfolio_results_rebalance[i][2],portfolio_results_rebalance[i][3],portfolio_results_rebalance[i][4],
                            portfolio_results_DCA[i][0],portfolio_results_DCA[i][1],portfolio_results_DCA[i][2],portfolio_results_DCA[i][3],portfolio_results_DCA[i][4],
                            portfolio_results_DCA_rebalance[i][0],portfolio_results_DCA_rebalance[i][1],portfolio_results_DCA_rebalance[i][2],portfolio_results_DCA_rebalance[i][3],portfolio_results_rebalance[i][4]]]
print(len(df2))
for row in final_array_return:
    df2.loc[len(df2)]=row

print(df2)
df2.to_csv("return.csv")

0
       1-OFF-1M   1-OFF-3M  1-OFF-6M  ...  DCA-REB-6M  DCA-REB-9M  DCA-REB-12M
0      1.179237   3.402843  0.840336  ...   -0.566814   -2.884167    -6.961303
1      1.311747   3.441825  1.589331  ...   -0.061309   -2.182750    -5.523978
2      1.448133   3.481947  2.360240  ...    0.444414   -1.478253    -4.073230
3      1.584499   3.522064  3.131031  ...    0.950348   -0.770701    -2.609037
4      1.720843   3.562174  3.901706  ...    1.456483   -0.060117    -1.131375
...         ...        ...       ...  ...         ...         ...          ...
10621  0.668069 -21.286315 -5.943124  ...    2.365414    4.455455     5.357597
10622  0.800444 -21.257073 -5.196430  ...    2.800729    5.145543     6.784547
10623  0.744637 -21.202294 -5.820005  ...    2.375408    4.553839     5.749319
10624  0.693054 -21.486512 -5.624974  ...    2.609172    4.684563     5.876788
10625  0.641588 -22.565321 -6.294537  ...    2.389875    4.761793     5.638748

[10626 rows x 20 columns]
